In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import os, sys
from collections import Counter

import seaborn as sns
import re

In [2]:
from catboost import CatBoostRegressor
from sklearn.model_selection import train_test_split
from sklearn import metrics

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import mean_absolute_error
from sklearn.metrics import mean_squared_error
from verstack.stratified_continuous_split import scsplit 

In [3]:
path = os.getcwd()
path_data_train = path + "\\covidChallenge\\data\\train.csv"
path_data_eval = path + "\\covidChallenge\\data\\evaluation.csv"

In [4]:
train_data = pd.read_csv(path_data_train)

In [5]:
train_data['urls'] = train_data['text'].apply(lambda s: len(re.findall(r'http(\S)+', s)))
train_data['hashtags'] = train_data['text'].apply(lambda s: len(re.findall(r'#[a-zA-Z]+', s)))
train_data['user_mentions'] = train_data['text'].apply(lambda s: len(re.findall(r'@[a-zA-Z_]+', s)))

In [6]:
#Non-relevant features, can not be used for LR models
train_data.drop('timestamp', axis=1, inplace=True)
train_data.drop('text', axis=1, inplace=True)
train_data.drop('id', axis=1, inplace=True)

In [7]:
#Convert boolean variables into int (Verified/Non-verified account)
train_data = train_data.astype(int)

In [8]:
train_data

retweet_count  user_verified  user_statuses_count  \
0                   0              0                68460   
1                   0              0                  309   
2                   0              0                 3241   
3                   0              0                32327   
4                   0              0                  581   
...               ...            ...                  ...   
665772              0              0                65355   
665773              1              0                 1807   
665774              8              0                  888   
665775              0              0                  452   
665776              0              0                  590   

        user_followers_count  user_friends_count  user_mentions  urls  \
0                       1101                1226              0     0   
1                         51                 202              0     0   
2                       1675                2325              0     0   
3                        667                 304              0     0   
4                         42                 127              0     0   
...                      ...                 ...            ...   ...   
665772                  1984                1902              0     0   
665773                  2029                 347              1     1   
665774                    85                 257              5     1   
665775                    38                  91              0     0   
665776                   184                 238              0     0   

        hashtags  
0              0  
1              0  
2              0  
3              0  
4              0  
...          ...  
665772         0  
665773         2  
665774         1  
665775         0  
665776         0  

[665777 rows x 8 columns]

### Splitting dataset

In [14]:
X_train, X_test, y_train, y_test = scsplit(train_data, train_data['retweet_count'], \
                                           stratify=train_data['retweet_count'], train_size=0.7, test_size=0.3, random_state = 42)

# We remove the actual number of retweets from our features since it is the value that we are trying to predict
X_train = X_train.drop(['retweet_count'], axis=1)
X_test = X_test.drop(['retweet_count'], axis=1)

In [39]:
print("\t Train dataset shape: ", X_train.shape)
print("\t Test dataset shape: ", X_test.shape)

	 Train dataset shape:  (466043, 7)
	 Test dataset shape:  (199734, 7)


### Model

In [25]:
model = CatBoostRegressor(iterations=3000, learning_rate=0.001, verbose = 1, task_type="GPU", devices='0')

In [26]:
model.fit(X_train, y_train)

0:	learn: 3029.2054514	total: 44.3ms	remaining: 2m 12s
1:	learn: 3029.0627464	total: 79.6ms	remaining: 1m 59s
2:	learn: 3028.9705462	total: 113ms	remaining: 1m 52s
3:	learn: 3028.8865145	total: 143ms	remaining: 1m 47s
4:	learn: 3028.7957018	total: 186ms	remaining: 1m 51s
5:	learn: 3028.6801857	total: 218ms	remaining: 1m 48s
6:	learn: 3028.6007890	total: 241ms	remaining: 1m 43s
7:	learn: 3028.4666921	total: 280ms	remaining: 1m 44s
8:	learn: 3028.3774457	total: 306ms	remaining: 1m 41s
9:	learn: 3028.2882895	total: 333ms	remaining: 1m 39s
10:	learn: 3028.1995950	total: 359ms	remaining: 1m 37s
11:	learn: 3028.1209288	total: 382ms	remaining: 1m 35s
12:	learn: 3027.9871822	total: 411ms	remaining: 1m 34s
13:	learn: 3027.8985718	total: 440ms	remaining: 1m 33s
14:	learn: 3027.8085655	total: 471ms	remaining: 1m 33s
15:	learn: 3027.6957984	total: 504ms	remaining: 1m 33s
16:	learn: 3027.6078298	total: 535ms	remaining: 1m 33s
17:	learn: 3027.5135416	total: 570ms	remaining: 1m 34s
18:	learn: 3027.43

153:	learn: 3015.7494448	total: 4.8s	remaining: 1m 28s
154:	learn: 3015.6787540	total: 4.83s	remaining: 1m 28s
155:	learn: 3015.6088076	total: 4.85s	remaining: 1m 28s
156:	learn: 3015.5052840	total: 4.88s	remaining: 1m 28s
157:	learn: 3015.4145348	total: 4.91s	remaining: 1m 28s
158:	learn: 3015.3554017	total: 4.93s	remaining: 1m 28s
159:	learn: 3015.2847016	total: 4.96s	remaining: 1m 28s
160:	learn: 3015.2062581	total: 4.99s	remaining: 1m 28s
161:	learn: 3015.1362075	total: 5.02s	remaining: 1m 27s
162:	learn: 3015.0443277	total: 5.05s	remaining: 1m 27s
163:	learn: 3014.9771651	total: 5.1s	remaining: 1m 28s
164:	learn: 3014.9180235	total: 5.12s	remaining: 1m 27s
165:	learn: 3014.8512312	total: 5.15s	remaining: 1m 27s
166:	learn: 3014.7914340	total: 5.17s	remaining: 1m 27s
167:	learn: 3014.7226799	total: 5.2s	remaining: 1m 27s
168:	learn: 3014.6636265	total: 5.22s	remaining: 1m 27s
169:	learn: 3014.6055049	total: 5.24s	remaining: 1m 27s
170:	learn: 3014.5460761	total: 5.27s	remaining: 1m

306:	learn: 3005.2399182	total: 9.12s	remaining: 1m 20s
307:	learn: 3005.1891949	total: 9.15s	remaining: 1m 20s
308:	learn: 3005.1335106	total: 9.18s	remaining: 1m 19s
309:	learn: 3005.0881200	total: 9.21s	remaining: 1m 19s
310:	learn: 3005.0415121	total: 9.23s	remaining: 1m 19s
311:	learn: 3004.9874161	total: 9.27s	remaining: 1m 19s
312:	learn: 3004.9109501	total: 9.3s	remaining: 1m 19s
313:	learn: 3004.8647138	total: 9.32s	remaining: 1m 19s
314:	learn: 3004.7666232	total: 9.35s	remaining: 1m 19s
315:	learn: 3004.6871562	total: 9.38s	remaining: 1m 19s
316:	learn: 3004.6324922	total: 9.4s	remaining: 1m 19s
317:	learn: 3004.5347685	total: 9.45s	remaining: 1m 19s
318:	learn: 3004.4799145	total: 9.47s	remaining: 1m 19s
319:	learn: 3004.4354502	total: 9.5s	remaining: 1m 19s
320:	learn: 3004.3604678	total: 9.53s	remaining: 1m 19s
321:	learn: 3004.3161890	total: 9.55s	remaining: 1m 19s
322:	learn: 3004.2712542	total: 9.57s	remaining: 1m 19s
323:	learn: 3004.2265060	total: 9.59s	remaining: 1m

457:	learn: 2997.3159505	total: 13.4s	remaining: 1m 14s
458:	learn: 2997.2078540	total: 13.5s	remaining: 1m 14s
459:	learn: 2997.1721025	total: 13.5s	remaining: 1m 14s
460:	learn: 2997.1093251	total: 13.7s	remaining: 1m 15s
461:	learn: 2997.0234616	total: 13.7s	remaining: 1m 15s
462:	learn: 2996.9890217	total: 13.7s	remaining: 1m 15s
463:	learn: 2996.9205160	total: 13.7s	remaining: 1m 15s
464:	learn: 2996.8782857	total: 13.8s	remaining: 1m 15s
465:	learn: 2996.8261070	total: 13.8s	remaining: 1m 14s
466:	learn: 2996.7911955	total: 13.8s	remaining: 1m 14s
467:	learn: 2996.7484003	total: 13.8s	remaining: 1m 14s
468:	learn: 2996.7135818	total: 13.9s	remaining: 1m 14s
469:	learn: 2996.6707855	total: 13.9s	remaining: 1m 14s
470:	learn: 2996.6374677	total: 13.9s	remaining: 1m 14s
471:	learn: 2996.6021786	total: 13.9s	remaining: 1m 14s
472:	learn: 2996.5385446	total: 13.9s	remaining: 1m 14s
473:	learn: 2996.5046623	total: 14s	remaining: 1m 14s
474:	learn: 2996.4704041	total: 14s	remaining: 1m 

607:	learn: 2991.2057571	total: 17.7s	remaining: 1m 9s
608:	learn: 2991.1641983	total: 17.8s	remaining: 1m 9s
609:	learn: 2991.1370250	total: 17.8s	remaining: 1m 9s
610:	learn: 2991.0960294	total: 17.9s	remaining: 1m 9s
611:	learn: 2991.0532467	total: 17.9s	remaining: 1m 9s
612:	learn: 2991.0195843	total: 17.9s	remaining: 1m 9s
613:	learn: 2990.9935380	total: 17.9s	remaining: 1m 9s
614:	learn: 2990.9597808	total: 18s	remaining: 1m 9s
615:	learn: 2990.9169022	total: 18s	remaining: 1m 9s
616:	learn: 2990.8617044	total: 18s	remaining: 1m 9s
617:	learn: 2990.8063175	total: 18.1s	remaining: 1m 9s
618:	learn: 2990.7756615	total: 18.1s	remaining: 1m 9s
619:	learn: 2990.7338146	total: 18.1s	remaining: 1m 9s
620:	learn: 2990.7067314	total: 18.1s	remaining: 1m 9s
621:	learn: 2990.6726889	total: 18.2s	remaining: 1m 9s
622:	learn: 2990.6304644	total: 18.2s	remaining: 1m 9s
623:	learn: 2990.5893678	total: 18.2s	remaining: 1m 9s
624:	learn: 2990.5627535	total: 18.3s	remaining: 1m 9s
625:	learn: 2990

...

2291:	learn: 2967.6410304	total: 1m 2s	remaining: 19.4s
2292:	learn: 2967.6401774	total: 1m 2s	remaining: 19.4s
2293:	learn: 2967.6388507	total: 1m 2s	remaining: 19.3s
2294:	learn: 2967.6321219	total: 1m 2s	remaining: 19.3s
2295:	learn: 2967.6057756	total: 1m 2s	remaining: 19.3s
2296:	learn: 2967.6049226	total: 1m 2s	remaining: 19.3s
2297:	learn: 2967.6031220	total: 1m 2s	remaining: 19.2s
2298:	learn: 2967.6022690	total: 1m 2s	remaining: 19.2s
2299:	learn: 2967.5979095	total: 1m 3s	remaining: 19.2s
2300:	learn: 2967.5921285	total: 1m 3s	remaining: 19.1s
2301:	learn: 2967.5910860	total: 1m 3s	remaining: 19.1s
2302:	learn: 2967.5865369	total: 1m 3s	remaining: 19.1s
2303:	learn: 2967.5817983	total: 1m 3s	remaining: 19.1s
2304:	learn: 2967.5753538	total: 1m 3s	remaining: 19s
2305:	learn: 2967.5660661	total: 1m 3s	remaining: 19s
2306:	learn: 2967.5274933	total: 1m 3s	remaining: 19s
2307:	learn: 2967.5264508	total: 1m 3s	remaining: 18.9s
2308:	learn: 2967.5254083	total: 1m 3s	remaining: 18.9

2438:	learn: 2966.4098975	total: 1m 6s	remaining: 15.3s
2439:	learn: 2966.4088545	total: 1m 6s	remaining: 15.3s
2440:	learn: 2966.3864794	total: 1m 6s	remaining: 15.3s
2441:	learn: 2966.3853416	total: 1m 6s	remaining: 15.2s
2442:	learn: 2966.3814544	total: 1m 6s	remaining: 15.2s
2443:	learn: 2966.3808855	total: 1m 6s	remaining: 15.2s
2444:	learn: 2966.3479861	total: 1m 6s	remaining: 15.1s
2445:	learn: 2966.3470380	total: 1m 6s	remaining: 15.1s
2446:	learn: 2966.3458054	total: 1m 6s	remaining: 15.1s
2447:	learn: 2966.3113885	total: 1m 6s	remaining: 15.1s
2448:	learn: 2966.3065531	total: 1m 6s	remaining: 15s
2449:	learn: 2966.3020021	total: 1m 6s	remaining: 15s
2450:	learn: 2966.3007695	total: 1m 6s	remaining: 15s
2451:	learn: 2966.2781090	total: 1m 6s	remaining: 15s
2452:	learn: 2966.2776350	total: 1m 6s	remaining: 14.9s
2453:	learn: 2966.2764972	total: 1m 6s	remaining: 14.9s
2454:	learn: 2966.2426484	total: 1m 6s	remaining: 14.9s
2455:	learn: 2966.2337358	total: 1m 7s	remaining: 14.8s


2586:	learn: 2965.1204897	total: 1m 10s	remaining: 11.2s
2587:	learn: 2965.1199206	total: 1m 10s	remaining: 11.2s
2588:	learn: 2965.1190670	total: 1m 10s	remaining: 11.2s
2589:	learn: 2965.1166008	total: 1m 10s	remaining: 11.1s
2590:	learn: 2965.1155575	total: 1m 10s	remaining: 11.1s
2591:	learn: 2965.1149884	total: 1m 10s	remaining: 11.1s
2592:	learn: 2965.1067363	total: 1m 10s	remaining: 11s
2593:	learn: 2965.0759095	total: 1m 10s	remaining: 11s
2594:	learn: 2965.0751506	total: 1m 10s	remaining: 11s
2595:	learn: 2965.0446080	total: 1m 10s	remaining: 11s
2596:	learn: 2965.0403396	total: 1m 10s	remaining: 10.9s
2597:	learn: 2965.0306645	total: 1m 10s	remaining: 10.9s
2598:	learn: 2964.9990780	total: 1m 10s	remaining: 10.9s
2599:	learn: 2964.9957581	total: 1m 10s	remaining: 10.8s
2600:	learn: 2964.9920588	total: 1m 10s	remaining: 10.8s
2601:	learn: 2964.9710957	total: 1m 10s	remaining: 10.8s
2602:	learn: 2964.9705266	total: 1m 10s	remaining: 10.8s
2603:	learn: 2964.9498480	total: 1m 10s

2737:	learn: 2964.1225849	total: 1m 13s	remaining: 7.08s
2738:	learn: 2964.1180305	total: 1m 13s	remaining: 7.05s
2739:	learn: 2964.1172714	total: 1m 14s	remaining: 7.02s
2740:	learn: 2964.1133812	total: 1m 14s	remaining: 6.99s
2741:	learn: 2964.1092064	total: 1m 14s	remaining: 6.97s
2742:	learn: 2964.0800770	total: 1m 14s	remaining: 6.94s
2743:	learn: 2964.0598666	total: 1m 14s	remaining: 6.91s
2744:	learn: 2964.0583485	total: 1m 14s	remaining: 6.88s
2745:	learn: 2964.0582536	total: 1m 14s	remaining: 6.86s
2746:	learn: 2964.0527503	total: 1m 14s	remaining: 6.83s
2747:	learn: 2964.0482907	total: 1m 14s	remaining: 6.8s
2748:	learn: 2964.0482907	total: 1m 14s	remaining: 6.78s
2749:	learn: 2964.0478162	total: 1m 14s	remaining: 6.75s
2750:	learn: 2964.0475316	total: 1m 14s	remaining: 6.72s
2751:	learn: 2964.0400356	total: 1m 14s	remaining: 6.7s
2752:	learn: 2964.0354811	total: 1m 14s	remaining: 6.67s
2753:	learn: 2964.0299778	total: 1m 14s	remaining: 6.64s
2754:	learn: 2964.0255181	total: 

2884:	learn: 2963.1271914	total: 1m 17s	remaining: 3.1s
2885:	learn: 2963.1083982	total: 1m 17s	remaining: 3.07s
2886:	learn: 2963.0801133	total: 1m 17s	remaining: 3.05s
2887:	learn: 2963.0797337	total: 1m 17s	remaining: 3.02s
2888:	learn: 2963.0770760	total: 1m 17s	remaining: 2.99s
2889:	learn: 2963.0561943	total: 1m 17s	remaining: 2.96s
2890:	learn: 2963.0487908	total: 1m 17s	remaining: 2.94s
2891:	learn: 2963.0467975	total: 1m 17s	remaining: 2.91s
2892:	learn: 2963.0461331	total: 1m 18s	remaining: 2.88s
2893:	learn: 2963.0423364	total: 1m 18s	remaining: 2.86s
2894:	learn: 2963.0403431	total: 1m 18s	remaining: 2.83s
2895:	learn: 2963.0211697	total: 1m 18s	remaining: 2.81s
2896:	learn: 2963.0150950	total: 1m 18s	remaining: 2.78s
2897:	learn: 2963.0144305	total: 1m 18s	remaining: 2.75s
2898:	learn: 2963.0113932	total: 1m 18s	remaining: 2.72s
2899:	learn: 2963.0076913	total: 1m 18s	remaining: 2.7s
2900:	learn: 2963.0073117	total: 1m 18s	remaining: 2.67s
2901:	learn: 2963.0020911	total: 

In [27]:
print("Score on Training data: ", model.score(X_train, y_train))

Score on Training data:  0.043647701219490576


In [28]:
ypred = model.predict(X_test)

In [29]:
print("\t Prediction error using MSE: ", mean_squared_error(y_true=y_test, y_pred=ypred))
print("\t Prediction error using MAE: ", mean_absolute_error(y_true=y_test, y_pred=ypred))

	 Prediction error using MSE:  7632031.84742809
	 Prediction error using MAE:  257.9382165922808


### Grid Search for Parameters

In [30]:
grid = {'learning_rate': [0.001, 0.03, 0.1],
        'depth': [6, 10, 12, 17],
        'l2_leaf_reg': [1, 3, 5, 7, 9]}

In [34]:
model1 = CatBoostRegressor(verbose = 1, task_type="GPU", devices='0')

In [35]:
grid_search_result = model1.grid_search(grid, 
                                       X=X_train, 
                                       y=y_train, 
                                       plot=True)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

bestTest = 3892.416105
bestIteration = 999
0:	loss: 3892.4161045	best: 3892.4161045 (0)	total: 1m 24s	remaining: 1h 22m 54s
bestTest = 3881.949385
bestIteration = 987
1:	loss: 3881.9493850	best: 3881.9493850 (1)	total: 3m 10s	remaining: 1h 32m 12s
bestTest = 3877.407075
bestIteration = 995
2:	loss: 3877.4070752	best: 3877.4070752 (2)	total: 4m 45s	remaining: 1h 30m 32s
bestTest = 3892.379435
bestIteration = 999
3:	loss: 3892.3794354	best: 3877.4070752 (2)	total: 5m 54s	remaining: 1h 22m 45s
bestTest = 3884.070293
bestIteration = 990
4:	loss: 3884.0702925	best: 3877.4070752 (2)	total: 7m 2s	remaining: 1h 17m 31s
bestTest = 3865.440472
bestIteration = 964
5:	loss: 3865.4404723	best: 3865.4404723 (5)	total: 8m 9s	remaining: 1h 13m 27s
bestTest = 3892.336444
bestIteration = 999
6:	loss: 3892.3364435	best: 3865.4404723 (5)	total: 9m 16s	remaining: 1h 10m 10s
bestTest = 3879.358651
bestIteration = 995
7:	loss: 3879.3586510	best: 3865.4404723 (5)	total: 10m 23s	remaining: 1h 7m 31s
bestTest =

In [37]:
grid_search_result['params']

{'depth': 10, 'l2_leaf_reg': 1, 'learning_rate': 0.1}

In [38]:
model1 = CatBoostRegressor(iterations=3000, verbose = 1, task_type="GPU", devices='0', depth = 10, l2_leaf_reg = 1, learning_rate= 0.1)

In [41]:
model1.fit(X_train, y_train)

0:	learn: 3011.8657095	total: 63.2ms	remaining: 1m 3s
1:	learn: 3000.9675480	total: 96.6ms	remaining: 48.2s
2:	learn: 2994.8769189	total: 124ms	remaining: 41.3s
3:	learn: 2983.5868987	total: 171ms	remaining: 42.7s
4:	learn: 2972.3929925	total: 220ms	remaining: 43.8s
5:	learn: 2967.0448649	total: 268ms	remaining: 44.5s
6:	learn: 2959.8560477	total: 323ms	remaining: 45.8s
7:	learn: 2957.7179989	total: 356ms	remaining: 44.2s
8:	learn: 2950.4880603	total: 405ms	remaining: 44.6s
9:	learn: 2944.6296100	total: 457ms	remaining: 45.2s
10:	learn: 2942.7804145	total: 505ms	remaining: 45.4s
11:	learn: 2934.3068374	total: 558ms	remaining: 45.9s
12:	learn: 2929.0389596	total: 607ms	remaining: 46.1s
13:	learn: 2924.9677902	total: 655ms	remaining: 46.1s
14:	learn: 2921.6151289	total: 710ms	remaining: 46.6s
15:	learn: 2919.7222672	total: 765ms	remaining: 47.1s
16:	learn: 2917.6723136	total: 812ms	remaining: 47s
17:	learn: 2915.4982174	total: 863ms	remaining: 47.1s
18:	learn: 2914.4925861	total: 918ms	r

155:	learn: 2745.9209254	total: 8.14s	remaining: 44s
156:	learn: 2744.8726346	total: 8.2s	remaining: 44s
157:	learn: 2744.6693430	total: 8.25s	remaining: 44s
158:	learn: 2743.5253419	total: 8.29s	remaining: 43.9s
159:	learn: 2743.3038044	total: 8.33s	remaining: 43.8s
160:	learn: 2743.1465337	total: 8.39s	remaining: 43.7s
161:	learn: 2742.9887413	total: 8.44s	remaining: 43.7s
162:	learn: 2742.8761587	total: 8.49s	remaining: 43.6s
163:	learn: 2742.7896167	total: 8.54s	remaining: 43.5s
164:	learn: 2742.4558301	total: 8.59s	remaining: 43.5s
165:	learn: 2742.4460876	total: 8.65s	remaining: 43.5s
166:	learn: 2742.3478407	total: 8.7s	remaining: 43.4s
167:	learn: 2742.3401490	total: 8.76s	remaining: 43.4s
168:	learn: 2742.2930752	total: 8.82s	remaining: 43.4s
169:	learn: 2742.1842589	total: 8.87s	remaining: 43.3s
170:	learn: 2742.0436425	total: 8.92s	remaining: 43.2s
171:	learn: 2741.6301619	total: 8.97s	remaining: 43.2s
172:	learn: 2741.5801010	total: 9.02s	remaining: 43.1s
173:	learn: 2741.5

305:	learn: 2734.1269302	total: 15.9s	remaining: 36.1s
306:	learn: 2734.1261072	total: 16s	remaining: 36s
307:	learn: 2734.1260044	total: 16s	remaining: 35.9s
308:	learn: 2734.1254901	total: 16s	remaining: 35.9s
309:	learn: 2734.1255929	total: 16.1s	remaining: 35.8s
310:	learn: 2734.1252843	total: 16.1s	remaining: 35.8s
311:	learn: 2734.1242557	total: 16.2s	remaining: 35.7s
312:	learn: 2734.1246671	total: 16.2s	remaining: 35.6s
313:	learn: 2734.1246671	total: 16.3s	remaining: 35.5s
314:	learn: 2734.1241528	total: 16.3s	remaining: 35.5s
315:	learn: 2734.1245643	total: 16.3s	remaining: 35.4s
316:	learn: 2734.1242557	total: 16.4s	remaining: 35.3s
317:	learn: 2734.1243586	total: 16.4s	remaining: 35.3s
318:	learn: 2734.1240500	total: 16.5s	remaining: 35.2s
319:	learn: 2734.1242557	total: 16.5s	remaining: 35.1s
320:	learn: 2734.1242557	total: 16.6s	remaining: 35.1s
321:	learn: 2734.1242557	total: 16.6s	remaining: 35s
322:	learn: 2734.1237414	total: 16.7s	remaining: 35s
323:	learn: 2734.12374

459:	learn: 2731.8700787	total: 23.2s	remaining: 27.3s
460:	learn: 2731.3588870	total: 23.3s	remaining: 27.2s
461:	learn: 2731.3059606	total: 23.3s	remaining: 27.2s
462:	learn: 2731.2829980	total: 23.4s	remaining: 27.1s
463:	learn: 2731.2821743	total: 23.4s	remaining: 27.1s
464:	learn: 2731.2811445	total: 23.5s	remaining: 27s
465:	learn: 2731.2809386	total: 23.5s	remaining: 27s
466:	learn: 2731.2798059	total: 23.6s	remaining: 26.9s
467:	learn: 2731.2782613	total: 23.6s	remaining: 26.8s
468:	learn: 2731.2774376	total: 23.6s	remaining: 26.8s
469:	learn: 2731.2778494	total: 23.7s	remaining: 26.7s
470:	learn: 2731.2772316	total: 23.7s	remaining: 26.7s
471:	learn: 2731.2774376	total: 23.8s	remaining: 26.6s
472:	learn: 2731.2769227	total: 23.8s	remaining: 26.5s
473:	learn: 2731.2766138	total: 23.9s	remaining: 26.5s
474:	learn: 2731.2756870	total: 23.9s	remaining: 26.4s
475:	learn: 2731.2759960	total: 24s	remaining: 26.4s
476:	learn: 2731.2753781	total: 24s	remaining: 26.3s
477:	learn: 2731.2

611:	learn: 2730.5534502	total: 30.3s	remaining: 19.2s
612:	learn: 2730.5533472	total: 30.3s	remaining: 19.1s
613:	learn: 2730.5533472	total: 30.4s	remaining: 19.1s
614:	learn: 2730.1901483	total: 30.4s	remaining: 19.1s
615:	learn: 2730.1300912	total: 30.5s	remaining: 19s
616:	learn: 2730.1286490	total: 30.5s	remaining: 19s
617:	learn: 2730.1287520	total: 30.6s	remaining: 18.9s
618:	learn: 2730.1285460	total: 30.6s	remaining: 18.9s
619:	learn: 2730.1282369	total: 30.7s	remaining: 18.8s
620:	learn: 2730.1270008	total: 30.7s	remaining: 18.8s
621:	learn: 2730.1275158	total: 30.8s	remaining: 18.7s
622:	learn: 2730.1266917	total: 30.8s	remaining: 18.7s
623:	learn: 2730.1268977	total: 30.9s	remaining: 18.6s
624:	learn: 2730.1266917	total: 30.9s	remaining: 18.5s
625:	learn: 2730.1262797	total: 31s	remaining: 18.5s
626:	learn: 2730.1266917	total: 31s	remaining: 18.4s
627:	learn: 2730.1266917	total: 31s	remaining: 18.4s
628:	learn: 2730.1266917	total: 31.1s	remaining: 18.3s
629:	learn: 2730.126

765:	learn: 2728.8936309	total: 37.7s	remaining: 11.5s
766:	learn: 2728.8924972	total: 37.7s	remaining: 11.5s
767:	learn: 2728.8920849	total: 37.8s	remaining: 11.4s
768:	learn: 2728.8924972	total: 37.8s	remaining: 11.4s
769:	learn: 2728.8918788	total: 37.9s	remaining: 11.3s
770:	learn: 2728.8915696	total: 37.9s	remaining: 11.3s
771:	learn: 2728.8910543	total: 38s	remaining: 11.2s
772:	learn: 2728.8902298	total: 38s	remaining: 11.2s
773:	learn: 2728.8896114	total: 38.1s	remaining: 11.1s
774:	learn: 2728.8903329	total: 38.1s	remaining: 11.1s
775:	learn: 2728.8901268	total: 38.2s	remaining: 11s
776:	learn: 2728.8891992	total: 38.2s	remaining: 11s
777:	learn: 2728.8890961	total: 38.3s	remaining: 10.9s
778:	learn: 2728.8893023	total: 38.3s	remaining: 10.9s
779:	learn: 2728.8896114	total: 38.4s	remaining: 10.8s
780:	learn: 2728.8895084	total: 38.4s	remaining: 10.8s
781:	learn: 2728.8889931	total: 38.5s	remaining: 10.7s
782:	learn: 2728.8889931	total: 38.5s	remaining: 10.7s
783:	learn: 2728.8

917:	learn: 2727.6454743	total: 45.8s	remaining: 4.09s
918:	learn: 2727.6457836	total: 45.9s	remaining: 4.05s
919:	learn: 2727.6459898	total: 46s	remaining: 4s
920:	learn: 2727.6458867	total: 46s	remaining: 3.95s
921:	learn: 2727.6464022	total: 46.1s	remaining: 3.9s
922:	learn: 2727.6459898	total: 46.1s	remaining: 3.85s
923:	learn: 2727.6465054	total: 46.2s	remaining: 3.8s
924:	learn: 2727.6459898	total: 46.3s	remaining: 3.75s
925:	learn: 2727.6465054	total: 46.3s	remaining: 3.7s
926:	learn: 2727.6459898	total: 46.4s	remaining: 3.65s
927:	learn: 2727.6462991	total: 46.4s	remaining: 3.6s
928:	learn: 2727.6464022	total: 46.5s	remaining: 3.55s
929:	learn: 2727.5208128	total: 46.5s	remaining: 3.5s
930:	learn: 2727.5123575	total: 46.6s	remaining: 3.45s
931:	learn: 2727.5126668	total: 46.7s	remaining: 3.4s
932:	learn: 2727.5120481	total: 46.7s	remaining: 3.35s
933:	learn: 2727.5118419	total: 46.8s	remaining: 3.31s
934:	learn: 2727.5120481	total: 46.8s	remaining: 3.25s
935:	learn: 2727.511429

In [42]:
print("Score on Training data: ", model1.score(X_train, y_train))

Score on Training data:  0.18942635542528907


In [43]:
ypred = model1.predict(X_test)

In [44]:
print("\t Prediction error using MSE: ", mean_squared_error(y_true=y_test, y_pred=ypred))
print("\t Prediction error using MAE: ", mean_absolute_error(y_true=y_test, y_pred=ypred))

	 Prediction error using MSE:  6866778.849680532
	 Prediction error using MAE:  230.99797917398038


-------------------------------------------------------------------

In [45]:
model2 = CatBoostRegressor(iterations=10000, verbose = 1, task_type="GPU", devices='0', depth = 10, l2_leaf_reg = 1, learning_rate= 0.1)

In [46]:
model2.fit(X_train, y_train)

0:	learn: 3011.8657095	total: 58.8ms	remaining: 9m 48s
1:	learn: 3000.9675480	total: 98.6ms	remaining: 8m 13s
2:	learn: 2994.8769189	total: 136ms	remaining: 7m 33s
3:	learn: 2983.5868987	total: 197ms	remaining: 8m 11s
4:	learn: 2972.3929925	total: 252ms	remaining: 8m 23s
5:	learn: 2967.0448649	total: 312ms	remaining: 8m 39s
6:	learn: 2959.8560477	total: 370ms	remaining: 8m 47s
7:	learn: 2957.7179989	total: 397ms	remaining: 8m 15s
8:	learn: 2950.4880603	total: 444ms	remaining: 8m 12s
9:	learn: 2944.6296100	total: 495ms	remaining: 8m 14s
10:	learn: 2942.7804145	total: 542ms	remaining: 8m 12s
11:	learn: 2934.3068374	total: 597ms	remaining: 8m 16s
12:	learn: 2929.0389596	total: 642ms	remaining: 8m 13s
13:	learn: 2924.9677902	total: 688ms	remaining: 8m 11s
14:	learn: 2921.6151289	total: 746ms	remaining: 8m 16s
15:	learn: 2919.7222672	total: 804ms	remaining: 8m 22s
16:	learn: 2917.6723136	total: 858ms	remaining: 8m 23s
17:	learn: 2915.4982174	total: 914ms	remaining: 8m 26s
18:	learn: 2914.49

150:	learn: 2746.3162483	total: 7.88s	remaining: 8m 34s
151:	learn: 2746.1105032	total: 7.94s	remaining: 8m 34s
152:	learn: 2746.0854113	total: 8s	remaining: 8m 34s
153:	learn: 2746.0720971	total: 8.05s	remaining: 8m 34s
154:	learn: 2745.9421268	total: 8.11s	remaining: 8m 35s
155:	learn: 2745.9209254	total: 8.16s	remaining: 8m 35s
156:	learn: 2744.8726346	total: 8.21s	remaining: 8m 35s
157:	learn: 2744.6693430	total: 8.26s	remaining: 8m 34s
158:	learn: 2743.5253419	total: 8.3s	remaining: 8m 33s
159:	learn: 2743.3038044	total: 8.35s	remaining: 8m 33s
160:	learn: 2743.1465337	total: 8.4s	remaining: 8m 33s
161:	learn: 2742.9887413	total: 8.44s	remaining: 8m 32s
162:	learn: 2742.8761587	total: 8.48s	remaining: 8m 31s
163:	learn: 2742.7896167	total: 8.53s	remaining: 8m 31s
164:	learn: 2742.4558301	total: 8.58s	remaining: 8m 31s
165:	learn: 2742.4460876	total: 8.63s	remaining: 8m 31s
166:	learn: 2742.3478407	total: 8.67s	remaining: 8m 30s
167:	learn: 2742.3401490	total: 8.73s	remaining: 8m 3

297:	learn: 2735.1193919	total: 15.7s	remaining: 8m 30s
298:	learn: 2735.1204202	total: 15.8s	remaining: 8m 31s
299:	learn: 2734.2061346	total: 15.8s	remaining: 8m 31s
300:	learn: 2734.1319705	total: 15.9s	remaining: 8m 31s
301:	learn: 2734.1302218	total: 15.9s	remaining: 8m 31s
302:	learn: 2734.1292960	total: 16s	remaining: 8m 31s
303:	learn: 2734.1286789	total: 16s	remaining: 8m 31s
304:	learn: 2734.1273416	total: 16.1s	remaining: 8m 31s
305:	learn: 2734.1269302	total: 16.2s	remaining: 8m 31s
306:	learn: 2734.1261072	total: 16.2s	remaining: 8m 31s
307:	learn: 2734.1260044	total: 16.3s	remaining: 8m 32s
308:	learn: 2734.1254901	total: 16.3s	remaining: 8m 32s
309:	learn: 2734.1255929	total: 16.4s	remaining: 8m 32s
310:	learn: 2734.1252843	total: 16.4s	remaining: 8m 32s
311:	learn: 2734.1242557	total: 16.5s	remaining: 8m 32s
312:	learn: 2734.1246671	total: 16.6s	remaining: 8m 32s
313:	learn: 2734.1246671	total: 16.6s	remaining: 8m 32s
314:	learn: 2734.1241528	total: 16.7s	remaining: 8m 

444:	learn: 2731.8706964	total: 23.7s	remaining: 8m 28s
445:	learn: 2731.8709023	total: 23.7s	remaining: 8m 28s
446:	learn: 2731.8705934	total: 23.8s	remaining: 8m 28s
447:	learn: 2731.8705934	total: 23.9s	remaining: 8m 28s
448:	learn: 2731.8700787	total: 23.9s	remaining: 8m 28s
449:	learn: 2731.8698728	total: 23.9s	remaining: 8m 28s
450:	learn: 2731.8703875	total: 24s	remaining: 8m 27s
451:	learn: 2731.8700787	total: 24s	remaining: 8m 27s
452:	learn: 2731.8704905	total: 24.1s	remaining: 8m 27s
453:	learn: 2731.8706964	total: 24.1s	remaining: 8m 27s
454:	learn: 2731.8713141	total: 24.2s	remaining: 8m 27s
455:	learn: 2731.8714170	total: 24.2s	remaining: 8m 26s
456:	learn: 2731.8714170	total: 24.3s	remaining: 8m 26s
457:	learn: 2731.8703875	total: 24.3s	remaining: 8m 26s
458:	learn: 2731.8705934	total: 24.4s	remaining: 8m 26s
459:	learn: 2731.8700787	total: 24.4s	remaining: 8m 26s
460:	learn: 2731.3588870	total: 24.5s	remaining: 8m 26s
461:	learn: 2731.3059606	total: 24.5s	remaining: 8m 

594:	learn: 2730.5537592	total: 31.6s	remaining: 8m 19s
595:	learn: 2730.5534502	total: 31.6s	remaining: 8m 19s
596:	learn: 2730.5530382	total: 31.7s	remaining: 8m 19s
597:	learn: 2730.5532442	total: 31.8s	remaining: 8m 19s
598:	learn: 2730.5530382	total: 31.8s	remaining: 8m 19s
599:	learn: 2730.5531412	total: 31.9s	remaining: 8m 19s
600:	learn: 2730.5524202	total: 31.9s	remaining: 8m 19s
601:	learn: 2730.5532442	total: 32s	remaining: 8m 19s
602:	learn: 2730.5533472	total: 32s	remaining: 8m 19s
603:	learn: 2730.5528322	total: 32.1s	remaining: 8m 19s
604:	learn: 2730.5530382	total: 32.1s	remaining: 8m 19s
605:	learn: 2730.5534502	total: 32.2s	remaining: 8m 19s
606:	learn: 2730.5532442	total: 32.3s	remaining: 8m 19s
607:	learn: 2730.5532442	total: 32.3s	remaining: 8m 19s
608:	learn: 2730.5532442	total: 32.4s	remaining: 8m 18s
609:	learn: 2730.5533472	total: 32.4s	remaining: 8m 18s
610:	learn: 2730.5531412	total: 32.4s	remaining: 8m 18s
611:	learn: 2730.5534502	total: 32.5s	remaining: 8m 

...

9292:	learn: 2708.0758392	total: 7m 48s	remaining: 35.6s
9293:	learn: 2708.0758392	total: 7m 48s	remaining: 35.6s
9294:	learn: 2708.0758392	total: 7m 48s	remaining: 35.5s
9295:	learn: 2708.0758392	total: 7m 48s	remaining: 35.5s
9296:	learn: 2708.0758392	total: 7m 48s	remaining: 35.4s
9297:	learn: 2708.0758392	total: 7m 48s	remaining: 35.4s
9298:	learn: 2708.0758392	total: 7m 48s	remaining: 35.3s
9299:	learn: 2708.0758392	total: 7m 48s	remaining: 35.3s
9300:	learn: 2708.0758392	total: 7m 48s	remaining: 35.2s
9301:	learn: 2708.0758392	total: 7m 48s	remaining: 35.2s
9302:	learn: 2708.0758392	total: 7m 48s	remaining: 35.1s
9303:	learn: 2708.0758392	total: 7m 48s	remaining: 35.1s
9304:	learn: 2708.0758392	total: 7m 48s	remaining: 35s
9305:	learn: 2708.0758392	total: 7m 49s	remaining: 35s
9306:	learn: 2708.0758392	total: 7m 49s	remaining: 34.9s
9307:	learn: 2708.0758392	total: 7m 49s	remaining: 34.9s
9308:	learn: 2708.0758392	total: 7m 49s	remaining: 34.8s
9309:	learn: 2708.0758392	total: 7m

9440:	learn: 2708.0758392	total: 7m 55s	remaining: 28.1s
9441:	learn: 2708.0758392	total: 7m 55s	remaining: 28.1s
9442:	learn: 2708.0758392	total: 7m 55s	remaining: 28s
9443:	learn: 2708.0758392	total: 7m 55s	remaining: 28s
9444:	learn: 2708.0758392	total: 7m 55s	remaining: 27.9s
9445:	learn: 2708.0758392	total: 7m 55s	remaining: 27.9s
9446:	learn: 2708.0758392	total: 7m 55s	remaining: 27.8s
9447:	learn: 2708.0758392	total: 7m 55s	remaining: 27.8s
9448:	learn: 2708.0758392	total: 7m 55s	remaining: 27.7s
9449:	learn: 2708.0758392	total: 7m 55s	remaining: 27.7s
9450:	learn: 2708.0758392	total: 7m 55s	remaining: 27.6s
9451:	learn: 2708.0758392	total: 7m 55s	remaining: 27.6s
9452:	learn: 2708.0758392	total: 7m 55s	remaining: 27.5s
9453:	learn: 2708.0758392	total: 7m 55s	remaining: 27.5s
9454:	learn: 2708.0758392	total: 7m 55s	remaining: 27.4s
9455:	learn: 2708.0758392	total: 7m 55s	remaining: 27.4s
9456:	learn: 2708.0758392	total: 7m 55s	remaining: 27.3s
9457:	learn: 2708.0758392	total: 7m

9588:	learn: 2708.0758392	total: 8m 1s	remaining: 20.7s
9589:	learn: 2708.0758392	total: 8m 1s	remaining: 20.6s
9590:	learn: 2708.0758392	total: 8m 1s	remaining: 20.6s
9591:	learn: 2708.0758392	total: 8m 1s	remaining: 20.5s
9592:	learn: 2708.0758392	total: 8m 2s	remaining: 20.4s
9593:	learn: 2708.0758392	total: 8m 2s	remaining: 20.4s
9594:	learn: 2708.0758392	total: 8m 2s	remaining: 20.3s
9595:	learn: 2708.0758392	total: 8m 2s	remaining: 20.3s
9596:	learn: 2708.0758392	total: 8m 2s	remaining: 20.2s
9597:	learn: 2708.0758392	total: 8m 2s	remaining: 20.2s
9598:	learn: 2708.0758392	total: 8m 2s	remaining: 20.1s
9599:	learn: 2708.0758392	total: 8m 2s	remaining: 20.1s
9600:	learn: 2708.0758392	total: 8m 2s	remaining: 20s
9601:	learn: 2708.0758392	total: 8m 2s	remaining: 20s
9602:	learn: 2708.0758392	total: 8m 2s	remaining: 19.9s
9603:	learn: 2708.0758392	total: 8m 2s	remaining: 19.9s
9604:	learn: 2708.0758392	total: 8m 2s	remaining: 19.8s
9605:	learn: 2708.0758392	total: 8m 2s	remaining: 19

9735:	learn: 2708.0758392	total: 8m 8s	remaining: 13.3s
9736:	learn: 2708.0758392	total: 8m 8s	remaining: 13.2s
9737:	learn: 2708.0758392	total: 8m 8s	remaining: 13.2s
9738:	learn: 2708.0758392	total: 8m 8s	remaining: 13.1s
9739:	learn: 2708.0758392	total: 8m 8s	remaining: 13.1s
9740:	learn: 2708.0758392	total: 8m 8s	remaining: 13s
9741:	learn: 2708.0758392	total: 8m 9s	remaining: 12.9s
9742:	learn: 2708.0758392	total: 8m 9s	remaining: 12.9s
9743:	learn: 2708.0758392	total: 8m 9s	remaining: 12.8s
9744:	learn: 2708.0758392	total: 8m 9s	remaining: 12.8s
9745:	learn: 2708.0758392	total: 8m 9s	remaining: 12.7s
9746:	learn: 2708.0758392	total: 8m 9s	remaining: 12.7s
9747:	learn: 2708.0758392	total: 8m 9s	remaining: 12.6s
9748:	learn: 2708.0758392	total: 8m 9s	remaining: 12.6s
9749:	learn: 2708.0758392	total: 8m 9s	remaining: 12.5s
9750:	learn: 2708.0758392	total: 8m 9s	remaining: 12.5s
9751:	learn: 2708.0758392	total: 8m 9s	remaining: 12.4s
9752:	learn: 2708.0758392	total: 8m 9s	remaining: 

9882:	learn: 2708.0758392	total: 8m 15s	remaining: 5.87s
9883:	learn: 2708.0758392	total: 8m 15s	remaining: 5.82s
9884:	learn: 2708.0758392	total: 8m 15s	remaining: 5.77s
9885:	learn: 2708.0758392	total: 8m 15s	remaining: 5.72s
9886:	learn: 2708.0758392	total: 8m 15s	remaining: 5.67s
9887:	learn: 2708.0758392	total: 8m 15s	remaining: 5.62s
9888:	learn: 2708.0758392	total: 8m 15s	remaining: 5.57s
9889:	learn: 2708.0758392	total: 8m 16s	remaining: 5.52s
9890:	learn: 2708.0758392	total: 8m 16s	remaining: 5.47s
9891:	learn: 2708.0758392	total: 8m 16s	remaining: 5.42s
9892:	learn: 2708.0758392	total: 8m 16s	remaining: 5.37s
9893:	learn: 2708.0758392	total: 8m 16s	remaining: 5.32s
9894:	learn: 2708.0758392	total: 8m 16s	remaining: 5.27s
9895:	learn: 2708.0758392	total: 8m 16s	remaining: 5.21s
9896:	learn: 2708.0758392	total: 8m 16s	remaining: 5.17s
9897:	learn: 2708.0758392	total: 8m 16s	remaining: 5.12s
9898:	learn: 2708.0758392	total: 8m 16s	remaining: 5.07s
9899:	learn: 2708.0758392	total

In [50]:
print("\t Score on Training data: ", model2.score(X_train, y_train))

	 Score on Training data:  0.20083611253040423


In [51]:
ypred = model2.predict(X_test)

In [52]:
print("\t Prediction error using MSE: ", mean_squared_error(y_true=y_test, y_pred=ypred))
print("\t Prediction error using MAE: ", mean_absolute_error(y_true=y_test, y_pred=ypred))

	 Prediction error using MSE:  6931174.789385914
	 Prediction error using MAE:  233.99963452971937


In [63]:
model3 = CatBoostRegressor(iterations=6000, verbose = 1, task_type="GPU", devices='0', depth = 10, l2_leaf_reg = 1, learning_rate= 0.01)

In [64]:
model3.fit(X_train, y_train)

0:	learn: 3027.4902246	total: 58.4ms	remaining: 5m 50s
1:	learn: 3026.1542583	total: 94.2ms	remaining: 4m 42s
2:	learn: 3025.2648977	total: 124ms	remaining: 4m 7s
3:	learn: 3023.5764570	total: 180ms	remaining: 4m 29s
4:	learn: 3021.7971667	total: 235ms	remaining: 4m 41s
5:	learn: 3020.5853135	total: 291ms	remaining: 4m 50s
6:	learn: 3018.8249426	total: 345ms	remaining: 4m 55s
7:	learn: 3017.2847426	total: 377ms	remaining: 4m 42s
8:	learn: 3015.0881692	total: 429ms	remaining: 4m 45s
9:	learn: 3013.5582851	total: 486ms	remaining: 4m 50s
10:	learn: 3012.6849971	total: 533ms	remaining: 4m 50s
11:	learn: 3010.4567606	total: 586ms	remaining: 4m 52s
12:	learn: 3009.3187528	total: 644ms	remaining: 4m 56s
13:	learn: 3007.5400047	total: 703ms	remaining: 5m
14:	learn: 3006.4346636	total: 755ms	remaining: 5m 1s
15:	learn: 3004.8351372	total: 806ms	remaining: 5m 1s
16:	learn: 3003.5932189	total: 853ms	remaining: 5m
17:	learn: 3002.6415391	total: 891ms	remaining: 4m 56s
18:	learn: 3001.2202008	total

152:	learn: 2903.0911709	total: 7.72s	remaining: 4m 55s
153:	learn: 2902.8002330	total: 7.78s	remaining: 4m 55s
154:	learn: 2902.0294892	total: 7.83s	remaining: 4m 55s
155:	learn: 2901.6631349	total: 7.88s	remaining: 4m 55s
156:	learn: 2901.1828305	total: 7.93s	remaining: 4m 55s
157:	learn: 2901.0305317	total: 7.99s	remaining: 4m 55s
158:	learn: 2900.9117699	total: 8.03s	remaining: 4m 55s
159:	learn: 2900.4152447	total: 8.09s	remaining: 4m 55s
160:	learn: 2900.0433526	total: 8.13s	remaining: 4m 55s
161:	learn: 2899.6508504	total: 8.19s	remaining: 4m 55s
162:	learn: 2899.2280292	total: 8.25s	remaining: 4m 55s
163:	learn: 2899.1379086	total: 8.3s	remaining: 4m 55s
164:	learn: 2898.7051161	total: 8.36s	remaining: 4m 55s
165:	learn: 2898.5112554	total: 8.41s	remaining: 4m 55s
166:	learn: 2898.4046167	total: 8.47s	remaining: 4m 55s
167:	learn: 2898.3483363	total: 8.51s	remaining: 4m 55s
168:	learn: 2898.2464466	total: 8.57s	remaining: 4m 55s
169:	learn: 2898.1222334	total: 8.62s	remaining: 

303:	learn: 2863.1030320	total: 14.8s	remaining: 4m 38s
304:	learn: 2863.0980223	total: 14.9s	remaining: 4m 37s
305:	learn: 2863.0576491	total: 14.9s	remaining: 4m 37s
306:	learn: 2862.9929134	total: 15s	remaining: 4m 37s
307:	learn: 2862.9419293	total: 15s	remaining: 4m 37s
308:	learn: 2862.7595971	total: 15.1s	remaining: 4m 37s
309:	learn: 2862.5983768	total: 15.1s	remaining: 4m 37s
310:	learn: 2862.3403660	total: 15.2s	remaining: 4m 37s
311:	learn: 2862.1712611	total: 15.2s	remaining: 4m 37s
312:	learn: 2861.9848508	total: 15.2s	remaining: 4m 37s
313:	learn: 2861.4931687	total: 15.3s	remaining: 4m 36s
314:	learn: 2861.3634284	total: 15.3s	remaining: 4m 36s
315:	learn: 2861.2221816	total: 15.4s	remaining: 4m 36s
316:	learn: 2860.9770229	total: 15.4s	remaining: 4m 36s
317:	learn: 2860.8541407	total: 15.4s	remaining: 4m 36s
318:	learn: 2860.8490287	total: 15.5s	remaining: 4m 35s
319:	learn: 2860.1613797	total: 15.5s	remaining: 4m 35s
320:	learn: 2859.9982428	total: 15.6s	remaining: 4m 

450:	learn: 2829.5935878	total: 20.9s	remaining: 4m 16s
451:	learn: 2829.5575075	total: 20.9s	remaining: 4m 16s
452:	learn: 2829.5563148	total: 21s	remaining: 4m 16s
453:	learn: 2828.6504804	total: 21s	remaining: 4m 16s
454:	learn: 2828.6498838	total: 21s	remaining: 4m 16s
455:	learn: 2828.3503935	total: 21.1s	remaining: 4m 16s
456:	learn: 2828.1883056	total: 21.1s	remaining: 4m 16s
457:	learn: 2828.1190922	total: 21.2s	remaining: 4m 16s
458:	learn: 2828.0919434	total: 21.2s	remaining: 4m 16s
459:	learn: 2828.0530594	total: 21.3s	remaining: 4m 16s
460:	learn: 2828.0143739	total: 21.3s	remaining: 4m 16s
461:	learn: 2827.9624608	total: 21.4s	remaining: 4m 16s
462:	learn: 2827.2888966	total: 21.4s	remaining: 4m 16s
463:	learn: 2827.2885982	total: 21.4s	remaining: 4m 15s
464:	learn: 2827.1369943	total: 21.5s	remaining: 4m 15s
465:	learn: 2827.1207789	total: 21.5s	remaining: 4m 15s
466:	learn: 2826.9821987	total: 21.6s	remaining: 4m 15s
467:	learn: 2826.8614204	total: 21.6s	remaining: 4m 15

600:	learn: 2805.4868669	total: 27.1s	remaining: 4m 3s
601:	learn: 2805.2968905	total: 27.2s	remaining: 4m 3s
602:	learn: 2804.9073736	total: 27.2s	remaining: 4m 3s
603:	learn: 2804.9040647	total: 27.2s	remaining: 4m 3s
604:	learn: 2804.8781953	total: 27.3s	remaining: 4m 3s
605:	learn: 2804.7202660	total: 27.3s	remaining: 4m 3s
606:	learn: 2804.6199888	total: 27.4s	remaining: 4m 3s
607:	learn: 2804.5549069	total: 27.4s	remaining: 4m 2s
608:	learn: 2804.5421712	total: 27.4s	remaining: 4m 2s
609:	learn: 2804.4562284	total: 27.5s	remaining: 4m 2s
610:	learn: 2804.4327617	total: 27.5s	remaining: 4m 2s
611:	learn: 2804.3445089	total: 27.6s	remaining: 4m 2s
612:	learn: 2804.3443083	total: 27.6s	remaining: 4m 2s
613:	learn: 2804.1910628	total: 27.6s	remaining: 4m 2s
614:	learn: 2804.1250683	total: 27.7s	remaining: 4m 2s
615:	learn: 2804.0603762	total: 27.7s	remaining: 4m 2s
616:	learn: 2804.0238671	total: 27.8s	remaining: 4m 2s
617:	learn: 2804.0071169	total: 27.8s	remaining: 4m 2s
618:	learn

...

5268:	learn: 2719.3022396	total: 4m 3s	remaining: 33.8s
5269:	learn: 2719.3022396	total: 4m 3s	remaining: 33.7s
5270:	learn: 2719.3022396	total: 4m 3s	remaining: 33.7s
5271:	learn: 2719.3022396	total: 4m 3s	remaining: 33.6s
5272:	learn: 2719.3022396	total: 4m 3s	remaining: 33.6s
5273:	learn: 2719.3022396	total: 4m 3s	remaining: 33.5s
5274:	learn: 2719.3022396	total: 4m 3s	remaining: 33.5s
5275:	learn: 2719.3022396	total: 4m 3s	remaining: 33.4s
5276:	learn: 2719.3022396	total: 4m 3s	remaining: 33.4s
5277:	learn: 2719.3022396	total: 4m 3s	remaining: 33.4s
5278:	learn: 2719.3022396	total: 4m 3s	remaining: 33.3s
5279:	learn: 2719.3022396	total: 4m 3s	remaining: 33.3s
5280:	learn: 2719.3022396	total: 4m 3s	remaining: 33.2s
5281:	learn: 2719.3022396	total: 4m 4s	remaining: 33.2s
5282:	learn: 2719.3022396	total: 4m 4s	remaining: 33.1s
5283:	learn: 2719.3022396	total: 4m 4s	remaining: 33.1s
5284:	learn: 2719.3022396	total: 4m 4s	remaining: 33s
5285:	learn: 2719.3022396	total: 4m 4s	remaining: 

5415:	learn: 2719.3022396	total: 4m 10s	remaining: 27s
5416:	learn: 2719.3022396	total: 4m 10s	remaining: 26.9s
5417:	learn: 2719.3022396	total: 4m 10s	remaining: 26.9s
5418:	learn: 2719.3022396	total: 4m 10s	remaining: 26.8s
5419:	learn: 2719.3022396	total: 4m 10s	remaining: 26.8s
5420:	learn: 2719.3022396	total: 4m 10s	remaining: 26.8s
5421:	learn: 2719.3022396	total: 4m 10s	remaining: 26.7s
5422:	learn: 2719.3022396	total: 4m 10s	remaining: 26.7s
5423:	learn: 2719.3022396	total: 4m 10s	remaining: 26.6s
5424:	learn: 2719.3022396	total: 4m 10s	remaining: 26.6s
5425:	learn: 2719.3022396	total: 4m 10s	remaining: 26.5s
5426:	learn: 2719.3022396	total: 4m 10s	remaining: 26.5s
5427:	learn: 2719.3022396	total: 4m 10s	remaining: 26.4s
5428:	learn: 2719.3022396	total: 4m 10s	remaining: 26.4s
5429:	learn: 2719.3022396	total: 4m 10s	remaining: 26.3s
5430:	learn: 2719.3022396	total: 4m 11s	remaining: 26.3s
5431:	learn: 2719.3022396	total: 4m 11s	remaining: 26.3s
5432:	learn: 2719.3022396	total: 

5562:	learn: 2719.3022396	total: 4m 18s	remaining: 20.3s
5563:	learn: 2719.3022396	total: 4m 18s	remaining: 20.3s
5564:	learn: 2719.3022396	total: 4m 18s	remaining: 20.2s
5565:	learn: 2719.3022396	total: 4m 18s	remaining: 20.2s
5566:	learn: 2719.3022396	total: 4m 18s	remaining: 20.1s
5567:	learn: 2719.3022396	total: 4m 18s	remaining: 20.1s
5568:	learn: 2719.3022396	total: 4m 18s	remaining: 20s
5569:	learn: 2719.3022396	total: 4m 18s	remaining: 20s
5570:	learn: 2719.3022396	total: 4m 18s	remaining: 19.9s
5571:	learn: 2719.3022396	total: 4m 18s	remaining: 19.9s
5572:	learn: 2719.3022396	total: 4m 18s	remaining: 19.8s
5573:	learn: 2719.3022396	total: 4m 18s	remaining: 19.8s
5574:	learn: 2719.3022396	total: 4m 18s	remaining: 19.7s
5575:	learn: 2719.3022396	total: 4m 18s	remaining: 19.7s
5576:	learn: 2719.3022396	total: 4m 19s	remaining: 19.6s
5577:	learn: 2719.3022396	total: 4m 19s	remaining: 19.6s
5578:	learn: 2719.3022396	total: 4m 19s	remaining: 19.6s
5579:	learn: 2719.3022396	total: 4m

5710:	learn: 2719.3022396	total: 4m 25s	remaining: 13.4s
5711:	learn: 2719.3022396	total: 4m 25s	remaining: 13.4s
5712:	learn: 2719.3022396	total: 4m 25s	remaining: 13.3s
5713:	learn: 2719.3022396	total: 4m 25s	remaining: 13.3s
5714:	learn: 2719.3022396	total: 4m 25s	remaining: 13.2s
5715:	learn: 2719.3022396	total: 4m 25s	remaining: 13.2s
5716:	learn: 2719.3022396	total: 4m 25s	remaining: 13.1s
5717:	learn: 2719.3022396	total: 4m 25s	remaining: 13.1s
5718:	learn: 2719.3022396	total: 4m 25s	remaining: 13.1s
5719:	learn: 2719.3022396	total: 4m 25s	remaining: 13s
5720:	learn: 2719.3022396	total: 4m 25s	remaining: 13s
5721:	learn: 2719.3022396	total: 4m 25s	remaining: 12.9s
5722:	learn: 2719.3022396	total: 4m 25s	remaining: 12.9s
5723:	learn: 2719.3022396	total: 4m 25s	remaining: 12.8s
5724:	learn: 2719.3022396	total: 4m 25s	remaining: 12.8s
5725:	learn: 2719.3022396	total: 4m 25s	remaining: 12.7s
5726:	learn: 2719.3022396	total: 4m 25s	remaining: 12.7s
5727:	learn: 2719.3022396	total: 4m

5856:	learn: 2719.3022396	total: 4m 31s	remaining: 6.64s
5857:	learn: 2719.3022396	total: 4m 31s	remaining: 6.59s
5858:	learn: 2719.3022396	total: 4m 32s	remaining: 6.55s
5859:	learn: 2719.3022396	total: 4m 32s	remaining: 6.5s
5860:	learn: 2719.3022396	total: 4m 32s	remaining: 6.45s
5861:	learn: 2719.3022396	total: 4m 32s	remaining: 6.41s
5862:	learn: 2719.3022396	total: 4m 32s	remaining: 6.36s
5863:	learn: 2719.3022396	total: 4m 32s	remaining: 6.31s
5864:	learn: 2719.3022396	total: 4m 32s	remaining: 6.27s
5865:	learn: 2719.3022396	total: 4m 32s	remaining: 6.22s
5866:	learn: 2719.3022396	total: 4m 32s	remaining: 6.18s
5867:	learn: 2719.3022396	total: 4m 32s	remaining: 6.13s
5868:	learn: 2719.3022396	total: 4m 32s	remaining: 6.08s
5869:	learn: 2719.3022396	total: 4m 32s	remaining: 6.04s
5870:	learn: 2719.3022396	total: 4m 32s	remaining: 5.99s
5871:	learn: 2719.3022396	total: 4m 32s	remaining: 5.94s
5872:	learn: 2719.3022396	total: 4m 32s	remaining: 5.9s
5873:	learn: 2719.3022396	total: 

In [65]:
print("\t Score on Training data: ", model3.score(X_train, y_train))

	 Score on Training data:  0.19419661587394443


In [66]:
ypred = model3.predict(X_test)

In [68]:
print("\t Prediction error using MSE: ", mean_squared_error(y_true=y_test, y_pred=ypred))
print("\t Prediction error using MAE: ", mean_absolute_error(y_true=y_test, y_pred=ypred))

	 Prediction error using MSE:  6872299.678280205
	 Prediction error using MAE:  230.21825239092325


In [69]:
evaluation = pd.read_csv(path_data_eval)
evaluation['urls'] = evaluation['text'].apply(lambda s: len(re.findall(r'http(\S)+', s)))
evaluation['hashtags'] = evaluation['text'].apply(lambda s: len(re.findall(r'#[a-zA-Z]+', s)))
evaluation['user_mentions'] = evaluation['text'].apply(lambda s: len(re.findall(r'@[a-zA-Z_]+', s)))

In [70]:
#Non-relevant features, can not be used for LR models
evaluation.drop('timestamp', axis=1, inplace=True)
evaluation.drop('text', axis=1, inplace=True)

In [71]:
evaluation

id  user_verified  user_statuses_count  user_followers_count  \
0       665776          False                  229                    36   
1       665777           True               106991                 41273   
2       665778          False                24127                   345   
3       665779           True                  771                  6555   
4       665780          False                32595                  6490   
...        ...            ...                  ...                   ...   
285329  951105           True                10532               6506208   
285330  951106          False                  151                   105   
285331  951107          False                  381                    77   
285332  951108           True                33982                974249   
285333  951109           True                87981               1106541   

        user_friends_count  user_mentions  urls  hashtags  
0                       99              0     0         0  
1                      326              0     0         0  
2                      200              0     0         0  
3                       83              0     2         0  
4                     1206              0     1         0  
...                    ...            ...   ...       ...  
285329                 119              0     1         5  
285330                 100              0     1         4  
285331                 210              0     0         0  
285332                 340              0     0         0  
285333                 381              0     1         0  

[285334 rows x 8 columns]

In [72]:
withoutID = evaluation.copy()
withoutID.drop('id', axis=1, inplace=True)

In [73]:
kaggleOut  =  model3.predict(withoutID)

import csv

f = open("CatRegressor_MAE230.txt", "w+")
with open("CatRegressor_MAE230.txt", 'w') as f:
    writer = csv.writer(f)
    writer.writerow(["TweetID", "NoRetweets"])
    for index, prediction in enumerate(kaggleOut):
        print(str(evaluation['id'].iloc[index]) + " ," + str(int(prediction)))
        writer.writerow([str(evaluation['id'].iloc[index]) , str(int(prediction))])

665776 ,43
665777 ,74
665778 ,53
665779 ,149
665780 ,384
665781 ,19
665782 ,31
665783 ,180
665784 ,227
665785 ,591
665786 ,794
665787 ,54
665788 ,57
665789 ,538
665790 ,60
665791 ,63
665792 ,70
665793 ,7
665794 ,416
665795 ,64
665796 ,3
665797 ,102
665798 ,396
665799 ,49
665800 ,18
665801 ,34
665802 ,34
665803 ,130
665804 ,87
665805 ,-25
665806 ,105
665807 ,46
665808 ,1461
665809 ,7
665810 ,31
665811 ,5
665812 ,9
665813 ,580
665814 ,36
665815 ,21
665816 ,57
665817 ,57
665818 ,61
665819 ,16
665820 ,-4
665821 ,40
665822 ,192
665823 ,34
665824 ,82
665825 ,187
665826 ,284
665827 ,56
665828 ,772
665829 ,-42
665830 ,370
665831 ,51
665832 ,54
665833 ,44
665834 ,51
665835 ,53
665836 ,57
665837 ,51
665838 ,541
665839 ,67
665840 ,27
665841 ,44
665842 ,7
665843 ,59
665844 ,4
665845 ,5
665846 ,441
665847 ,35
665848 ,193
665849 ,35
665850 ,196
665851 ,82
665852 ,1
665853 ,21
665854 ,223
665855 ,42
665856 ,16
665857 ,14
665858 ,58
665859 ,300
665860 ,586
665861 ,283
665862 ,31
665863 ,49
665864 ,322

667041 ,35
667042 ,38
667043 ,56
667044 ,26
667045 ,63
667046 ,140
667047 ,-40
667048 ,73
667049 ,29
667050 ,13
667051 ,57
667052 ,283
667053 ,57
667054 ,57
667055 ,1403
667056 ,62
667057 ,277
667058 ,537
667059 ,19
667060 ,51
667061 ,473
667062 ,27
667063 ,91
667064 ,2
667065 ,11
667066 ,144
667067 ,370
667068 ,57
667069 ,41
667070 ,46
667071 ,58
667072 ,175
667073 ,31
667074 ,320
667075 ,36
667076 ,32
667077 ,63
667078 ,51
667079 ,94
667080 ,212
667081 ,19
667082 ,98
667083 ,53
667084 ,743
667085 ,114
667086 ,370
667087 ,23
667088 ,63
667089 ,142
667090 ,18
667091 ,25
667092 ,56
667093 ,136
667094 ,56
667095 ,64
667096 ,216
667097 ,4
667098 ,153
667099 ,63
667100 ,60
667101 ,189
667102 ,81
667103 ,20
667104 ,110
667105 ,344
667106 ,44
667107 ,1
667108 ,285
667109 ,7
667110 ,33
667111 ,8
667112 ,497
667113 ,-33
667114 ,57
667115 ,33
667116 ,38
667117 ,422
667118 ,235
667119 ,49
667120 ,266
667121 ,53
667122 ,73
667123 ,805
667124 ,248
667125 ,16
667126 ,-3
667127 ,267
667128 ,219
6671

668088 ,39
668089 ,15
668090 ,663
668091 ,61
668092 ,90
668093 ,53
668094 ,50
668095 ,18
668096 ,66
668097 ,60
668098 ,65
668099 ,165
668100 ,53
668101 ,59
668102 ,101
668103 ,25
668104 ,204
668105 ,56
668106 ,55
668107 ,91
668108 ,121
668109 ,16
668110 ,-27
668111 ,76
668112 ,55
668113 ,21
668114 ,16
668115 ,30
668116 ,58
668117 ,61
668118 ,812
668119 ,29
668120 ,61
668121 ,21
668122 ,55
668123 ,9
668124 ,50
668125 ,48
668126 ,63
668127 ,56
668128 ,56
668129 ,57
668130 ,961
668131 ,50
668132 ,248
668133 ,31
668134 ,25
668135 ,59
668136 ,55
668137 ,331
668138 ,80
668139 ,36
668140 ,109
668141 ,53
668142 ,473
668143 ,60
668144 ,669
668145 ,45
668146 ,19
668147 ,19
668148 ,16
668149 ,11
668150 ,229
668151 ,114
668152 ,69
668153 ,261
668154 ,-18
668155 ,49
668156 ,175
668157 ,62
668158 ,317
668159 ,56
668160 ,-7
668161 ,64
668162 ,59
668163 ,36
668164 ,86
668165 ,8
668166 ,62
668167 ,35
668168 ,32
668169 ,48
668170 ,42
668171 ,117
668172 ,56
668173 ,7
668174 ,66
668175 ,100
668176 ,49
668

668895 ,418
668896 ,28
668897 ,66
668898 ,50
668899 ,456
668900 ,301
668901 ,58
668902 ,65
668903 ,360
668904 ,27
668905 ,288
668906 ,-16
668907 ,370
668908 ,4
668909 ,69
668910 ,16
668911 ,69
668912 ,38
668913 ,15
668914 ,12
668915 ,154
668916 ,15
668917 ,549
668918 ,47
668919 ,22
668920 ,16
668921 ,56
668922 ,387
668923 ,50
668924 ,1324
668925 ,64
668926 ,48
668927 ,20
668928 ,149
668929 ,47
668930 ,12
668931 ,65
668932 ,270
668933 ,-111
668934 ,36
668935 ,15
668936 ,62
668937 ,159
668938 ,210
668939 ,51
668940 ,54
668941 ,303
668942 ,726
668943 ,57
668944 ,81
668945 ,19
668946 ,57
668947 ,54
668948 ,57
668949 ,61
668950 ,64
668951 ,459
668952 ,107
668953 ,32
668954 ,50
668955 ,39
668956 ,65
668957 ,79
668958 ,271
668959 ,161
668960 ,50
668961 ,406
668962 ,56
668963 ,14
668964 ,49
668965 ,19
668966 ,31
668967 ,65
668968 ,26
668969 ,380
668970 ,49
668971 ,109
668972 ,64
668973 ,46
668974 ,51
668975 ,49
668976 ,90
668977 ,54
668978 ,87
668979 ,44
668980 ,15
668981 ,17
668982 ,4
668983 

670025 ,303
670026 ,53
670027 ,-13
670028 ,21
670029 ,37
670030 ,57
670031 ,138
670032 ,36
670033 ,56
670034 ,25
670035 ,5
670036 ,36
670037 ,55
670038 ,19
670039 ,48
670040 ,58
670041 ,283
670042 ,13
670043 ,1531
670044 ,64
670045 ,88
670046 ,15
670047 ,19
670048 ,126
670049 ,57
670050 ,63
670051 ,56
670052 ,91
670053 ,-21
670054 ,1116
670055 ,58
670056 ,58
670057 ,76
670058 ,9
670059 ,29
670060 ,54
670061 ,56
670062 ,85
670063 ,35
670064 ,57
670065 ,430
670066 ,1150
670067 ,19
670068 ,57
670069 ,71
670070 ,403
670071 ,109
670072 ,-42
670073 ,71
670074 ,76
670075 ,19
670076 ,292
670077 ,15
670078 ,303
670079 ,35
670080 ,141
670081 ,409
670082 ,56
670083 ,59
670084 ,129
670085 ,55
670086 ,72
670087 ,28
670088 ,8
670089 ,112
670090 ,337
670091 ,111
670092 ,242
670093 ,35
670094 ,63
670095 ,60
670096 ,567
670097 ,19
670098 ,60
670099 ,59
670100 ,65
670101 ,218
670102 ,55
670103 ,69
670104 ,380
670105 ,50
670106 ,58
670107 ,19
670108 ,63
670109 ,61
670110 ,136
670111 ,58
670112 ,49
670113

...

946158 ,5
946159 ,78
946160 ,55
946161 ,59
946162 ,6
946163 ,4469
946164 ,17
946165 ,68
946166 ,63
946167 ,117
946168 ,215
946169 ,51
946170 ,13
946171 ,56
946172 ,69
946173 ,313
946174 ,32
946175 ,65
946176 ,47
946177 ,63
946178 ,88
946179 ,34
946180 ,481
946181 ,358
946182 ,210
946183 ,14
946184 ,20
946185 ,5
946186 ,56
946187 ,40
946188 ,377
946189 ,108
946190 ,157
946191 ,18
946192 ,56
946193 ,60
946194 ,12
946195 ,197
946196 ,43
946197 ,724
946198 ,13
946199 ,50
946200 ,57
946201 ,35
946202 ,32
946203 ,60
946204 ,51
946205 ,64
946206 ,58
946207 ,235
946208 ,1835
946209 ,83
946210 ,40
946211 ,284
946212 ,1909
946213 ,-11
946214 ,55
946215 ,325
946216 ,38
946217 ,15
946218 ,35
946219 ,53
946220 ,35
946221 ,60
946222 ,512
946223 ,1784
946224 ,64
946225 ,30
946226 ,-15
946227 ,17
946228 ,243
946229 ,13
946230 ,87
946231 ,16
946232 ,16
946233 ,56
946234 ,20
946235 ,55
946236 ,65
946237 ,59
946238 ,69
946239 ,341
946240 ,339
946241 ,-3
946242 ,91
946243 ,54
946244 ,34
946245 ,606
946246

946950 ,742
946951 ,56
946952 ,56
946953 ,83
946954 ,49
946955 ,395
946956 ,154
946957 ,50
946958 ,17
946959 ,54
946960 ,104
946961 ,45
946962 ,38
946963 ,29
946964 ,57
946965 ,66
946966 ,60
946967 ,44
946968 ,61
946969 ,104
946970 ,-24
946971 ,61
946972 ,48
946973 ,256
946974 ,112
946975 ,56
946976 ,80
946977 ,584
946978 ,55
946979 ,63
946980 ,395
946981 ,412
946982 ,68
946983 ,214
946984 ,22
946985 ,63
946986 ,308
946987 ,208
946988 ,51
946989 ,13
946990 ,1309
946991 ,15
946992 ,44
946993 ,138
946994 ,19
946995 ,19
946996 ,56
946997 ,312
946998 ,192
946999 ,15
947000 ,63
947001 ,62
947002 ,208
947003 ,37
947004 ,17
947005 ,45
947006 ,57
947007 ,133
947008 ,47
947009 ,97
947010 ,32
947011 ,15
947012 ,463
947013 ,168
947014 ,358
947015 ,54
947016 ,19
947017 ,13
947018 ,29
947019 ,56
947020 ,64
947021 ,301
947022 ,63
947023 ,33
947024 ,63
947025 ,50
947026 ,29
947027 ,24
947028 ,67
947029 ,47
947030 ,-17
947031 ,50
947032 ,25
947033 ,517
947034 ,23
947035 ,16
947036 ,1221
947037 ,56
947

947834 ,128
947835 ,17
947836 ,23
947837 ,6
947838 ,94
947839 ,10
947840 ,31
947841 ,80
947842 ,-43
947843 ,61
947844 ,63
947845 ,44
947846 ,55
947847 ,88
947848 ,63
947849 ,-29
947850 ,52
947851 ,14
947852 ,65
947853 ,58
947854 ,21
947855 ,45
947856 ,50
947857 ,284
947858 ,55
947859 ,34
947860 ,57
947861 ,5
947862 ,53
947863 ,55
947864 ,44
947865 ,61
947866 ,425
947867 ,91
947868 ,53
947869 ,112
947870 ,65
947871 ,91
947872 ,152
947873 ,43
947874 ,32
947875 ,65
947876 ,18
947877 ,58
947878 ,94
947879 ,50
947880 ,64
947881 ,17
947882 ,3477
947883 ,158
947884 ,67
947885 ,65
947886 ,271
947887 ,71
947888 ,8
947889 ,52
947890 ,157
947891 ,49
947892 ,43
947893 ,272
947894 ,552
947895 ,111
947896 ,7
947897 ,386
947898 ,281
947899 ,63
947900 ,51
947901 ,878
947902 ,50
947903 ,55
947904 ,26
947905 ,87
947906 ,52
947907 ,2
947908 ,63
947909 ,54
947910 ,66
947911 ,27
947912 ,66
947913 ,43
947914 ,51
947915 ,56
947916 ,22
947917 ,102
947918 ,58
947919 ,58
947920 ,8
947921 ,395
947922 ,63
947923 

949471 ,119
949472 ,53
949473 ,9474
949474 ,57
949475 ,15
949476 ,64
949477 ,53
949478 ,12
949479 ,121
949480 ,64
949481 ,33
949482 ,55
949483 ,2
949484 ,301
949485 ,57
949486 ,52
949487 ,66
949488 ,58
949489 ,235
949490 ,204
949491 ,20
949492 ,271
949493 ,56
949494 ,335
949495 ,25
949496 ,559
949497 ,49
949498 ,68
949499 ,48
949500 ,60
949501 ,288
949502 ,65
949503 ,57
949504 ,60
949505 ,-8
949506 ,379
949507 ,60
949508 ,26
949509 ,26
949510 ,25
949511 ,64
949512 ,61
949513 ,28
949514 ,55
949515 ,311
949516 ,18
949517 ,212
949518 ,320
949519 ,422
949520 ,40
949521 ,146
949522 ,16
949523 ,519
949524 ,-33
949525 ,29
949526 ,291
949527 ,65
949528 ,63
949529 ,42
949530 ,80
949531 ,295
949532 ,34
949533 ,53
949534 ,406
949535 ,13
949536 ,55
949537 ,12
949538 ,100
949539 ,88
949540 ,-46
949541 ,121
949542 ,35
949543 ,62
949544 ,351
949545 ,56
949546 ,-11
949547 ,58
949548 ,178
949549 ,255
949550 ,285
949551 ,13
949552 ,15
949553 ,172
949554 ,56
949555 ,54
949556 ,59
949557 ,17
949558 ,31
94

950343 ,39
950344 ,1
950345 ,470
950346 ,54
950347 ,29
950348 ,99
950349 ,541
950350 ,-8
950351 ,56
950352 ,102
950353 ,64
950354 ,65
950355 ,337
950356 ,140
950357 ,31
950358 ,-23
950359 ,64
950360 ,57
950361 ,55
950362 ,78
950363 ,56
950364 ,277
950365 ,32
950366 ,166
950367 ,60
950368 ,244
950369 ,237
950370 ,31
950371 ,62
950372 ,58
950373 ,55
950374 ,28
950375 ,44
950376 ,13
950377 ,63
950378 ,34
950379 ,55
950380 ,31
950381 ,65
950382 ,64
950383 ,53
950384 ,67
950385 ,53
950386 ,59
950387 ,13
950388 ,63
950389 ,33
950390 ,91
950391 ,50
950392 ,394
950393 ,-6
950394 ,144
950395 ,36
950396 ,141
950397 ,66
950398 ,51
950399 ,35
950400 ,30
950401 ,22
950402 ,56
950403 ,55
950404 ,315
950405 ,23
950406 ,334
950407 ,19
950408 ,67
950409 ,11
950410 ,56
950411 ,56
950412 ,7
950413 ,63
950414 ,15
950415 ,220
950416 ,562
950417 ,59
950418 ,-4
950419 ,121
950420 ,16
950421 ,56
950422 ,65
950423 ,44
950424 ,384
950425 ,34
950426 ,136
950427 ,12
950428 ,31
950429 ,198
950430 ,20
950431 ,13
95

### Less features

In [11]:
train_data.columns

Index(['retweet_count', 'user_verified', 'user_statuses_count',
       'user_followers_count', 'user_friends_count', 'user_mentions', 'urls',
       'hashtags'],
      dtype='object')

In [12]:
#Non-relevant features, can not be used for LR models
train_data.drop('hashtags', axis=1, inplace=True)
train_data.drop('urls', axis=1, inplace=True)

In [13]:
X_train, X_test, y_train, y_test = scsplit(train_data, train_data['retweet_count'], \
                                           stratify=train_data['retweet_count'], train_size=0.7, test_size=0.3, random_state = 42)

# We remove the actual number of retweets from our features since it is the value that we are trying to predict
X_train = X_train.drop(['retweet_count'], axis=1)
X_test = X_test.drop(['retweet_count'], axis=1)

In [14]:
params = {'depth': 10, 'l2_leaf_reg': 1, 'learning_rate': 0.1}

In [17]:
model = CatBoostRegressor(iterations=5000, verbose = 1, task_type="GPU", devices='0', depth = 10, l2_leaf_reg = 1, learning_rate= 0.001)

In [18]:
model.fit(X_train, y_train)

0:	learn: 3029.1929174	total: 51.8ms	remaining: 4m 18s
1:	learn: 3028.9166919	total: 104ms	remaining: 4m 19s
2:	learn: 3028.8126017	total: 142ms	remaining: 3m 56s
3:	learn: 3028.6377482	total: 194ms	remaining: 4m 2s
4:	learn: 3028.5491569	total: 221ms	remaining: 3m 40s
5:	learn: 3028.4620488	total: 247ms	remaining: 3m 25s
6:	learn: 3028.2568056	total: 301ms	remaining: 3m 34s
7:	learn: 3028.1263157	total: 353ms	remaining: 3m 39s
8:	learn: 3027.9441777	total: 395ms	remaining: 3m 38s
9:	learn: 3027.8053144	total: 434ms	remaining: 3m 36s
10:	learn: 3027.6926401	total: 477ms	remaining: 3m 36s
11:	learn: 3027.4879021	total: 530ms	remaining: 3m 40s
12:	learn: 3027.2945774	total: 578ms	remaining: 3m 41s
13:	learn: 3027.1669261	total: 626ms	remaining: 3m 43s
14:	learn: 3027.0005254	total: 660ms	remaining: 3m 39s
15:	learn: 3026.7545776	total: 713ms	remaining: 3m 42s
16:	learn: 3026.6581257	total: 751ms	remaining: 3m 40s
17:	learn: 3026.5324919	total: 798ms	remaining: 3m 40s
18:	learn: 3026.4037

150:	learn: 3005.0795098	total: 6.68s	remaining: 3m 34s
151:	learn: 3004.9911598	total: 6.73s	remaining: 3m 34s
152:	learn: 3004.7421937	total: 6.78s	remaining: 3m 34s
153:	learn: 3004.5861581	total: 6.82s	remaining: 3m 34s
154:	learn: 3004.4905858	total: 6.87s	remaining: 3m 34s
155:	learn: 3004.2206081	total: 6.92s	remaining: 3m 34s
156:	learn: 3003.9437716	total: 6.97s	remaining: 3m 35s
157:	learn: 3003.7581073	total: 7.02s	remaining: 3m 35s
158:	learn: 3003.5234592	total: 7.06s	remaining: 3m 35s
159:	learn: 3003.3738217	total: 7.11s	remaining: 3m 35s
160:	learn: 3003.2590134	total: 7.16s	remaining: 3m 35s
161:	learn: 3003.0967198	total: 7.2s	remaining: 3m 35s
162:	learn: 3003.0118704	total: 7.24s	remaining: 3m 34s
163:	learn: 3002.7537485	total: 7.29s	remaining: 3m 34s
164:	learn: 3002.5274522	total: 7.34s	remaining: 3m 35s
165:	learn: 3002.4335941	total: 7.38s	remaining: 3m 34s
166:	learn: 3002.2983285	total: 7.4s	remaining: 3m 34s
167:	learn: 3002.1909735	total: 7.42s	remaining: 3

300:	learn: 2984.1838121	total: 13.3s	remaining: 3m 27s
301:	learn: 2984.0854187	total: 13.3s	remaining: 3m 26s
302:	learn: 2983.9596890	total: 13.3s	remaining: 3m 26s
303:	learn: 2983.7589253	total: 13.4s	remaining: 3m 26s
304:	learn: 2983.6816324	total: 13.4s	remaining: 3m 26s
305:	learn: 2983.5129949	total: 13.5s	remaining: 3m 26s
306:	learn: 2983.4290026	total: 13.5s	remaining: 3m 26s
307:	learn: 2983.3640506	total: 13.6s	remaining: 3m 26s
308:	learn: 2983.1871932	total: 13.6s	remaining: 3m 26s
309:	learn: 2983.0752849	total: 13.6s	remaining: 3m 26s
310:	learn: 2982.8693702	total: 13.7s	remaining: 3m 26s
311:	learn: 2982.7567899	total: 13.7s	remaining: 3m 26s
312:	learn: 2982.6078078	total: 13.8s	remaining: 3m 25s
313:	learn: 2982.5135115	total: 13.8s	remaining: 3m 25s
314:	learn: 2982.2967130	total: 13.8s	remaining: 3m 25s
315:	learn: 2982.1933534	total: 13.9s	remaining: 3m 25s
316:	learn: 2981.9996386	total: 13.9s	remaining: 3m 25s
317:	learn: 2981.7660136	total: 14s	remaining: 3

451:	learn: 2967.4704388	total: 20s	remaining: 3m 21s
452:	learn: 2967.2724455	total: 20.1s	remaining: 3m 21s
453:	learn: 2967.0717849	total: 20.1s	remaining: 3m 21s
454:	learn: 2966.8967053	total: 20.2s	remaining: 3m 21s
455:	learn: 2966.7771675	total: 20.2s	remaining: 3m 21s
456:	learn: 2966.7230374	total: 20.3s	remaining: 3m 21s
457:	learn: 2966.5255630	total: 20.3s	remaining: 3m 21s
458:	learn: 2966.3759554	total: 20.4s	remaining: 3m 21s
459:	learn: 2966.3289289	total: 20.4s	remaining: 3m 21s
460:	learn: 2966.2050066	total: 20.5s	remaining: 3m 21s
461:	learn: 2966.1566499	total: 20.5s	remaining: 3m 21s
462:	learn: 2965.9659652	total: 20.6s	remaining: 3m 21s
463:	learn: 2965.8982602	total: 20.6s	remaining: 3m 21s
464:	learn: 2965.7013948	total: 20.7s	remaining: 3m 21s
465:	learn: 2965.5739373	total: 20.7s	remaining: 3m 21s
466:	learn: 2965.3790421	total: 20.7s	remaining: 3m 21s
467:	learn: 2965.1599474	total: 20.8s	remaining: 3m 21s
468:	learn: 2964.9616102	total: 20.8s	remaining: 3

599:	learn: 2952.6949722	total: 26.7s	remaining: 3m 16s
600:	learn: 2952.6081981	total: 26.8s	remaining: 3m 16s
601:	learn: 2952.5291371	total: 26.8s	remaining: 3m 16s
602:	learn: 2952.3440500	total: 26.9s	remaining: 3m 16s
603:	learn: 2952.2516450	total: 26.9s	remaining: 3m 16s
604:	learn: 2952.1450422	total: 27s	remaining: 3m 15s
605:	learn: 2952.0734000	total: 27s	remaining: 3m 15s
606:	learn: 2951.9387802	total: 27.1s	remaining: 3m 15s
607:	learn: 2951.8364536	total: 27.1s	remaining: 3m 15s
608:	learn: 2951.7029664	total: 27.2s	remaining: 3m 15s
609:	learn: 2951.5750951	total: 27.2s	remaining: 3m 15s
610:	learn: 2951.4012879	total: 27.3s	remaining: 3m 15s
611:	learn: 2951.3632662	total: 27.3s	remaining: 3m 15s
612:	learn: 2951.2309965	total: 27.3s	remaining: 3m 15s
613:	learn: 2951.1886842	total: 27.4s	remaining: 3m 15s
614:	learn: 2951.1394143	total: 27.4s	remaining: 3m 15s
615:	learn: 2951.0810900	total: 27.5s	remaining: 3m 15s
616:	learn: 2951.0288639	total: 27.5s	remaining: 3m 

...

4271:	learn: 2855.6740339	total: 3m 2s	remaining: 31.1s
4272:	learn: 2855.6716702	total: 3m 2s	remaining: 31s
4273:	learn: 2855.6715717	total: 3m 2s	remaining: 31s
4274:	learn: 2855.6711778	total: 3m 2s	remaining: 31s
4275:	learn: 2855.6636928	total: 3m 2s	remaining: 30.9s
4276:	learn: 2855.6456697	total: 3m 2s	remaining: 30.9s
4277:	learn: 2855.6397605	total: 3m 2s	remaining: 30.8s
4278:	learn: 2855.6321769	total: 3m 2s	remaining: 30.8s
4279:	learn: 2855.6255783	total: 3m 2s	remaining: 30.7s
4280:	learn: 2855.6228206	total: 3m 2s	remaining: 30.7s
4281:	learn: 2855.6195705	total: 3m 2s	remaining: 30.7s
4282:	learn: 2855.6155325	total: 3m 2s	remaining: 30.6s
4283:	learn: 2855.6139567	total: 3m 2s	remaining: 30.6s
4284:	learn: 2855.5654016	total: 3m 2s	remaining: 30.5s
4285:	learn: 2855.5620529	total: 3m 3s	remaining: 30.5s
4286:	learn: 2855.5569314	total: 3m 3s	remaining: 30.4s
4287:	learn: 2855.5490522	total: 3m 3s	remaining: 30.4s
4288:	learn: 2855.4806005	total: 3m 3s	remaining: 30.4

4420:	learn: 2854.2744977	total: 3m 8s	remaining: 24.7s
4421:	learn: 2854.2396163	total: 3m 8s	remaining: 24.7s
4422:	learn: 2854.1982310	total: 3m 8s	remaining: 24.6s
4423:	learn: 2854.1876875	total: 3m 8s	remaining: 24.6s
4424:	learn: 2854.1807899	total: 3m 8s	remaining: 24.5s
4425:	learn: 2854.1684727	total: 3m 8s	remaining: 24.5s
4426:	learn: 2854.1677829	total: 3m 8s	remaining: 24.5s
4427:	learn: 2854.1676844	total: 3m 9s	remaining: 24.4s
4428:	learn: 2854.1600969	total: 3m 9s	remaining: 24.4s
4429:	learn: 2854.1527065	total: 3m 9s	remaining: 24.3s
4430:	learn: 2854.1464986	total: 3m 9s	remaining: 24.3s
4431:	learn: 2854.1463015	total: 3m 9s	remaining: 24.2s
4432:	learn: 2854.1454147	total: 3m 9s	remaining: 24.2s
4433:	learn: 2854.1417687	total: 3m 9s	remaining: 24.2s
4434:	learn: 2854.1415716	total: 3m 9s	remaining: 24.1s
4435:	learn: 2854.1390096	total: 3m 9s	remaining: 24.1s
4436:	learn: 2854.1274805	total: 3m 9s	remaining: 24s
4437:	learn: 2854.1272834	total: 3m 9s	remaining: 

4567:	learn: 2852.7859434	total: 3m 15s	remaining: 18.5s
4568:	learn: 2852.7652403	total: 3m 15s	remaining: 18.4s
4569:	learn: 2852.7622827	total: 3m 15s	remaining: 18.4s
4570:	learn: 2852.7550859	total: 3m 15s	remaining: 18.3s
4571:	learn: 2852.7521283	total: 3m 15s	remaining: 18.3s
4572:	learn: 2852.7437484	total: 3m 15s	remaining: 18.3s
4573:	learn: 2852.7397063	total: 3m 15s	remaining: 18.2s
4574:	learn: 2852.7394105	total: 3m 15s	remaining: 18.2s
4575:	learn: 2852.7337910	total: 3m 15s	remaining: 18.1s
4576:	learn: 2852.7291574	total: 3m 15s	remaining: 18.1s
4577:	learn: 2852.7213689	total: 3m 15s	remaining: 18s
4578:	learn: 2852.7144678	total: 3m 15s	remaining: 18s
4579:	learn: 2852.7066793	total: 3m 15s	remaining: 18s
4580:	learn: 2852.7062849	total: 3m 15s	remaining: 17.9s
4581:	learn: 2852.6712857	total: 3m 15s	remaining: 17.9s
4582:	learn: 2852.6636943	total: 3m 15s	remaining: 17.8s
4583:	learn: 2852.6498917	total: 3m 15s	remaining: 17.8s
4584:	learn: 2852.6441734	total: 3m 1

4716:	learn: 2851.4871731	total: 3m 21s	remaining: 12.1s
4717:	learn: 2851.4833265	total: 3m 21s	remaining: 12.1s
4718:	learn: 2851.4753373	total: 3m 21s	remaining: 12s
4719:	learn: 2851.4648824	total: 3m 21s	remaining: 12s
4720:	learn: 2851.4575837	total: 3m 22s	remaining: 11.9s
4721:	learn: 2851.4526521	total: 3m 22s	remaining: 11.9s
4722:	learn: 2851.4061960	total: 3m 22s	remaining: 11.9s
4723:	learn: 2851.3983053	total: 3m 22s	remaining: 11.8s
4724:	learn: 2851.3907105	total: 3m 22s	remaining: 11.8s
4725:	learn: 2851.3910064	total: 3m 22s	remaining: 11.7s
4726:	learn: 2851.3853843	total: 3m 22s	remaining: 11.7s
4727:	learn: 2851.3792689	total: 3m 22s	remaining: 11.6s
4728:	learn: 2851.3736468	total: 3m 22s	remaining: 11.6s
4729:	learn: 2851.3734495	total: 3m 22s	remaining: 11.6s
4730:	learn: 2851.3538211	total: 3m 22s	remaining: 11.5s
4731:	learn: 2851.3147612	total: 3m 22s	remaining: 11.5s
4732:	learn: 2851.3115062	total: 3m 22s	remaining: 11.4s
4733:	learn: 2851.2998670	total: 3m

4864:	learn: 2849.5932274	total: 3m 28s	remaining: 5.78s
4865:	learn: 2849.5932274	total: 3m 28s	remaining: 5.74s
4866:	learn: 2849.5927339	total: 3m 28s	remaining: 5.69s
4867:	learn: 2849.5911548	total: 3m 28s	remaining: 5.65s
4868:	learn: 2849.5895757	total: 3m 28s	remaining: 5.61s
4869:	learn: 2849.5760542	total: 3m 28s	remaining: 5.56s
4870:	learn: 2849.5728959	total: 3m 28s	remaining: 5.52s
4871:	learn: 2849.5293702	total: 3m 28s	remaining: 5.48s
4872:	learn: 2849.5264092	total: 3m 28s	remaining: 5.44s
4873:	learn: 2849.5238431	total: 3m 28s	remaining: 5.39s
4874:	learn: 2849.5129862	total: 3m 28s	remaining: 5.35s
4875:	learn: 2849.5127888	total: 3m 28s	remaining: 5.31s
4876:	learn: 2849.4995631	total: 3m 28s	remaining: 5.26s
4877:	learn: 2849.4961086	total: 3m 28s	remaining: 5.22s
4878:	learn: 2849.4872256	total: 3m 28s	remaining: 5.18s
4879:	learn: 2849.4516934	total: 3m 28s	remaining: 5.14s
4880:	learn: 2849.4498180	total: 3m 28s	remaining: 5.09s
4881:	learn: 2849.4343219	total

In [19]:
print("Score on Training data: ", model.score(X_train, y_train))

Score on Training data:  0.11578838249771994


In [20]:
ypred = model.predict(X_test)

In [21]:
print("\t Prediction error using MSE: ", mean_squared_error(y_true=y_test, y_pred=ypred))
print("\t Prediction error using MAE: ", mean_absolute_error(y_true=y_test, y_pred=ypred))

	 Prediction error using MSE:  6945692.995564764
	 Prediction error using MAE:  234.1374772513244


In [22]:
ypred

array([ 75.30357043,  97.67735934, 101.85207951, ...,  98.30344224,
       347.53617884,  48.2821373 ])